In [ ]:
import cv2

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from PIL import Image

from sklearn.model_selection import train_test_split

from tensorflow.keras import models, layers
from tensorflow.keras.utils import to_categorical

import cv2
import numpy as np
import time


# ignore//to isolate the hand region

In [ ]:

cam = cv2.VideoCapture(0)
time.sleep(2)
i = 0
while True:
    ret,frame = cam.read()
    #cv2.imshow('webcam', frame)
    cv2.imwrite('captures/'+str(i)+'.jpg',frame)
    i+=1
    if cv2.waitKey(1)&0xFF == ord('q'):
        break

In [ ]:
cam.release()
cv2.destroyAllWindows(

In [ ]:
# organize imports
import cv2
import imutils
import numpy as np

# global variables
bg = None

In [ ]:
#--------------------------------------------------
# To find the running average over the background
#--------------------------------------------------
def run_avg(image, aWeight):
    global bg
    # initialize the background
    if bg is None:
        bg = image.copy().astype("float")
        return

    # compute weighted average, accumulate it and update the background
    cv2.accumulateWeighted(image, bg, aWeight)

In [ ]:
#---------------------------------------------
# To segment the region of hand in the image
#---------------------------------------------
def segment(image, threshold=25):
    global bg
    # find the absolute difference between background and current frame
    diff = cv2.absdiff(bg.astype("uint8"), image)

    # threshold the diff image so that we get the foreground
    thresholded = cv2.threshold(diff, threshold, 255, cv2.THRESH_BINARY)[1]

    # get the contours in the thresholded image
    (_, cnts, _) = cv2.findContours(thresholded.copy(), cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    # return None, if no contours detected
    if len(cnts) == 0:
        return
    else:
        # based on contour area, get the maximum contour which is the hand
        segmented = max(cnts, key=cv2.contourArea)
        return (thresholded, segmented)

In [ ]:
#-----------------
# MAIN FUNCTION
#-----------------
if __name__ == "__main__":
    # initialize weight for running average
    aWeight = 0.5

    # get the reference to the webcam
    camera = cv2.VideoCapture(0)

    # region of interest (ROI) coordinates
    top, right, bottom, left = 10, 350, 225, 590

    # initialize num of frames
    num_frames = 0
    # keep looping, until interrupted
    while(True):
        # get the current frame
        (grabbed, frame) = camera.read()

        # resize the frame
        frame = imutils.resize(frame, width=700)

        # flip the frame so that it is not the mirror view
        frame = cv2.flip(frame, 1)

        # clone the frame
        clone = frame.copy()

        # get the height and width of the frame
        (height, width) = frame.shape[:2]

        # get the ROI
        roi = frame[top:bottom, right:left]

        # convert the roi to grayscale and blur it
        gray = cv2.cvtColor(roi, cv2.COLOR_BGR2GRAY)
        gray = cv2.GaussianBlur(gray, (7, 7), 0)

        # to get the background, keep looking till a threshold is reached
        # so that our running average model gets calibrated
        if num_frames < 30:
            run_avg(gray, aWeight)
        else:
            # segment the hand region
            hand = segment(gray)

            # check whether hand region is segmented
            if hand is not None:
                # if yes, unpack the thresholded image and
                # segmented region
                (thresholded, segmented) = hand

                # draw the segmented region and display the frame
                cv2.drawContours(clone, [segmented + (right, top)], -1, (0, 0, 255))
                #cv2.imshow("Thesholded", thresholded)
                cv2.imwrite('captures/'+str(num_frames)+'.jpg',thresholded)

        # draw the segmented hand
        cv2.rectangle(clone, (left, top), (right, bottom), (0,255,0), 2)

        # increment the number of frames
        num_frames += 1

        # display the frame with segmented hand
        cv2.imshow("Video Feed", clone)
        

        # observe the keypress by the user
        keypress = cv2.waitKey(1) & 0xFF

        # if the user pressed "q", then stop looping
        if keypress == ord("q"):
            break

# free up memory


In [ ]:
camera.release()
cv2.destroyAllWindows()

# live video capture with mediapipe

In [ ]:
import mediapipe as mp

In [ ]:
pip install mediapipe

In [ ]:
import cv2
import mediapipe as mp
mp_drawing = mp.solutions.drawing_utils
mp_drawing_styles = mp.solutions.drawing_styles
mp_hands = mp.solutions.hands


In [ ]:
# For webcam input:
cap = cv2.VideoCapture(0)
with mp_hands.Hands(
    min_detection_confidence=0.5,
    min_tracking_confidence=0.5) as hands:
    while cap.isOpened():
        success, image = cap.read()
        if not success:
            print("Ignoring empty camera frame.")
        # If loading a video, use 'break' instead of 'continue'.
            continue

    # Flip the image horizontally for a later selfie-view display, and convert
    # the BGR image to RGB.
        image = cv2.cvtColor(cv2.flip(image, 1), cv2.COLOR_BGR2RGB)
    # To improve performance, optionally mark the image as not writeable to
    # pass by reference.
        image.flags.writeable = False
        results = hands.process(image)

    # Draw the hand annotations on the image.
        image.flags.writeable = True
        image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
        if results.multi_hand_landmarks:
            for hand_landmarks in results.multi_hand_landmarks:
                mp_drawing.draw_landmarks(
                  image,
                  hand_landmarks,
                  mp_hands.HAND_CONNECTIONS,
                  mp_drawing_styles.get_default_hand_landmarks_style(),
                  mp_drawing_styles.get_default_hand_connections_style())
        cv2.imshow('MediaPipe Hands', image)
        if cv2.waitKey(5) & 0xFF == 27:
            break


In [ ]:
cap.release()

# preprocess the dataset

In [ ]:
from IPython.display import Image
Image("asl/amer_sign2.png")

In [ ]:
# Read Dataset
train = pd.read_csv('asl/sign_mnist_train.csv')
test = pd.read_csv('asl/sign_mnist_test.csv')

In [ ]:
train.head()

In [ ]:
labels = train['label']

In [ ]:
# droping the label coloumn from the training set
train.drop('label', axis = 1, inplace = True)
print(train.shape)

In [ ]:
x_train = train.values.reshape(train.shape[0],28,28,1)

In [ ]:
x_train.shape

In [ ]:
plt.imshow(x_train[0].reshape(28,28), cmap='gray')

In [ ]:
plt.imsave("cropped/0.png",x_train[0].reshape(28,28),cmap='gray')

In [ ]:
def crop(x_train):
    for i in range(len(x_train)):
        plt.imsave("cropped/cropped"+str(i)+".png",x_train[i].reshape(28,28),cmap='gray')

# images belong to the same folder 

In [5]:
import os
os.getcwd()

'/Users/bridgetliu/project/mais2021'

In [6]:
# loop thru all the files in a folder 
filenames = []
directory = '/Users/bridgetliu/project/mais2021/archive/asl_alphabet_train/asl_alphabet_train/K'
for filename in os.listdir(directory):
    if filename.endswith(".jpg") or filename.endswith(".png"):
        filenames.append(os.path.join(directory, filename))
    else:
        continue

In [7]:
import pandas as pd
dfObj = pd.DataFrame(columns=['LetterLabel', 'Handedness', 'Landmarks'])


In [8]:
import cv2
import mediapipe as mp
mp_drawing = mp.solutions.drawing_utils
mp_drawing_styles = mp.solutions.drawing_styles
mp_hands = mp.solutions.hands

IMAGE_FILES = filenames
#IMAGE_FILES = ["archive/asl_alphabet_train/asl_alphabet_train/K/K294.jpg"]
#IMAGE_FILES = ["test.jpg"]
all_img_features = []
with mp_hands.Hands(
    static_image_mode=True,
    max_num_hands=2,
    min_detection_confidence=0.5) as hands:
    for idx, file in enumerate(IMAGE_FILES):
        # print("here")
        featurelist = []
        # Read an image, flip it around y-axis for correct handedness output
        image = cv2.flip(cv2.imread(file), 1)
        # Convert the BGR image to RGB before processing.
        results = hands.process(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
        #results = hands.process(image)
        #Print handedness and draw hand landmarks on the image.
        #featurelist.append('k')
        #featurelist.append(results.multi_handedness)
        print('Handedness:', results.multi_handedness)
        if not results.multi_hand_landmarks:
            continue
        
        image_height, image_width, _ = image.shape
        annotated_image = image.copy()
        
        for hand_landmarks in results.multi_hand_landmarks:
            #featurelist.append(hand_landmarks)
            print('hand_landmarks:', hand_landmarks)
            print(
               f'Index finger tip coordinates: (',
               f'{hand_landmarks.landmark[mp_hands.HandLandmark.INDEX_FINGER_TIP].x * image_width}, '
               f'{hand_landmarks.landmark[mp_hands.HandLandmark.INDEX_FINGER_TIP].y * image_height})'
            )
            '''
            mp_drawing.draw_landmarks(
               annotated_image,
               hand_landmarks,
               mp_hands.HAND_CONNECTIONS,
               mp_drawing_styles.get_default_hand_landmarks_style(),
               mp_drawing_styles.get_default_hand_connections_style())
            '''
        #cv2.imwrite(
        #'/Users/bridgetliu/project/mais2021/tmp'+str(idx)+'.png', cv2.flip(annotated_image, 1))
        all_img_features.append(featurelist)
        dfObj = dfObj.append({'LetterLabel': 'k', 'Handedness': results.multi_handedness, 'Landmarks': hand_landmarks}, ignore_index=True)


here
Handedness: [classification {
  index: 1
  score: 0.9886448383331299
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.4801557660102844
  y: 0.8388364315032959
  z: 0.0
}
landmark {
  x: 0.4005644917488098
  y: 0.7655258178710938
  z: -0.04537683352828026
}
landmark {
  x: 0.3765736222267151
  y: 0.6439965963363647
  z: -0.06598800420761108
}
landmark {
  x: 0.44767099618911743
  y: 0.5601357817649841
  z: -0.08871569484472275
}
landmark {
  x: 0.5221688747406006
  y: 0.5200292468070984
  z: -0.10799865424633026
}
landmark {
  x: 0.4016893804073334
  y: 0.5369374752044678
  z: -0.020228136330842972
}
landmark {
  x: 0.368516206741333
  y: 0.40451014041900635
  z: -0.06344713270664215
}
landmark {
  x: 0.3516581654548645
  y: 0.3233761489391327
  z: -0.0837494358420372
}
landmark {
  x: 0.34731072187423706
  y: 0.24876007437705994
  z: -0.09949949383735657
}
landmark {
  x: 0.48485952615737915
  y: 0.5566457509994507
  z: -0.038441166281700134
}
landmark {
  x: 0.5214462876319

hand_landmarks: landmark {
  x: 0.42300066351890564
  y: 0.8345731496810913
  z: 0.0
}
landmark {
  x: 0.35346540808677673
  y: 0.7575842142105103
  z: -0.04144066199660301
}
landmark {
  x: 0.34057241678237915
  y: 0.6330421566963196
  z: -0.05844569951295853
}
landmark {
  x: 0.4085769057273865
  y: 0.5467591285705566
  z: -0.07626333087682724
}
landmark {
  x: 0.4790285527706146
  y: 0.4996280074119568
  z: -0.09022922068834305
}
landmark {
  x: 0.3463340699672699
  y: 0.5408000349998474
  z: -0.013537907972931862
}
landmark {
  x: 0.32133108377456665
  y: 0.4115549623966217
  z: -0.04683448001742363
}
landmark {
  x: 0.3111448287963867
  y: 0.32867228984832764
  z: -0.060834795236587524
}
landmark {
  x: 0.31101194024086
  y: 0.2551482021808624
  z: -0.07293737679719925
}
landmark {
  x: 0.42567920684814453
  y: 0.5579132437705994
  z: -0.029300415888428688
}
landmark {
  x: 0.4732476770877838
  y: 0.4144677519798279
  z: -0.07311319559812546
}
landmark {
  x: 0.5114699602127075
  

Handedness: None
here
Handedness: [classification {
  index: 1
  score: 0.7824877500534058
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.6376370787620544
  y: 0.8884994983673096
  z: 0.0
}
landmark {
  x: 0.563994288444519
  y: 0.8211758732795715
  z: 0.0020039533264935017
}
landmark {
  x: 0.5689462423324585
  y: 0.733947217464447
  z: 0.004624185152351856
}
landmark {
  x: 0.628774881362915
  y: 0.6837937831878662
  z: 0.009847987443208694
}
landmark {
  x: 0.676613986492157
  y: 0.6616091728210449
  z: 0.018077289685606956
}
landmark {
  x: 0.6008530259132385
  y: 0.6575592756271362
  z: -0.035778939723968506
}
landmark {
  x: 0.6057884097099304
  y: 0.5367173552513123
  z: -0.05155950412154198
}
landmark {
  x: 0.6162061095237732
  y: 0.4655998945236206
  z: -0.06156814098358154
}
landmark {
  x: 0.6287054419517517
  y: 0.3998020887374878
  z: -0.07065130025148392
}
landmark {
  x: 0.6717615723609924
  y: 0.6780639886856079
  z: -0.040728259831666946
}
landmark {
  x: 0.73

Handedness: [classification {
  index: 1
  score: 0.9823909401893616
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.3294069468975067
  y: 0.5758030414581299
  z: 0.0
}
landmark {
  x: 0.2743303179740906
  y: 0.5041269659996033
  z: -0.02677760273218155
}
landmark {
  x: 0.2596869468688965
  y: 0.4087989628314972
  z: -0.03768971562385559
}
landmark {
  x: 0.3096371591091156
  y: 0.3409390151500702
  z: -0.0518442839384079
}
landmark {
  x: 0.3668021261692047
  y: 0.30604884028434753
  z: -0.06241557002067566
}
landmark {
  x: 0.2880317270755768
  y: 0.3407275080680847
  z: 0.009233781136572361
}
landmark {
  x: 0.27201616764068604
  y: 0.2490013986825943
  z: -0.017797963693737984
}
landmark {
  x: 0.266439825296402
  y: 0.19080586731433868
  z: -0.02989587001502514
}
landmark {
  x: 0.26773273944854736
  y: 0.13954275846481323
  z: -0.037262991070747375
}
landmark {
  x: 0.3420933187007904
  y: 0.3504580855369568
  z: -0.0009836290264502168
}
landmark {
  x: 0.3681823313236236

Handedness: None
here
Handedness: [classification {
  index: 1
  score: 0.9938540458679199
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.5597175359725952
  y: 0.8080834150314331
  z: 0.0
}
landmark {
  x: 0.4600874185562134
  y: 0.7277572751045227
  z: -0.07200838625431061
}
landmark {
  x: 0.44098833203315735
  y: 0.5863827466964722
  z: -0.0921168401837349
}
landmark {
  x: 0.5466575622558594
  y: 0.483163058757782
  z: -0.10948410630226135
}
landmark {
  x: 0.6426694393157959
  y: 0.42794302105903625
  z: -0.12299376726150513
}
landmark {
  x: 0.42750751972198486
  y: 0.4746423363685608
  z: -0.009359410963952541
}
landmark {
  x: 0.40396618843078613
  y: 0.31789371371269226
  z: -0.04892844706773758
}
landmark {
  x: 0.3925696015357971
  y: 0.2126886546611786
  z: -0.07058454304933548
}
landmark {
  x: 0.39415040612220764
  y: 0.12081781029701233
  z: -0.08914390206336975
}
landmark {
  x: 0.5371994972229004
  y: 0.49449247121810913
  z: -0.01705700159072876
}
landmark {
 

...

Handedness: [classification {
  index: 1
  score: 0.9816926121711731
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.3410623371601105
  y: 0.9209800958633423
  z: 0.0
}
landmark {
  x: 0.22016391158103943
  y: 0.8684254884719849
  z: -0.050862714648246765
}
landmark {
  x: 0.17213411629199982
  y: 0.7348790764808655
  z: -0.08759822696447372
}
landmark {
  x: 0.22215697169303894
  y: 0.6353803277015686
  z: -0.1288345456123352
}
landmark {
  x: 0.29247820377349854
  y: 0.5686383247375488
  z: -0.1708010733127594
}
landmark {
  x: 0.20315270125865936
  y: 0.5769070982933044
  z: -0.06731259077787399
}
landmark {
  x: 0.15660957992076874
  y: 0.4138171374797821
  z: -0.13960236310958862
}
landmark {
  x: 0.14129893481731415
  y: 0.30221253633499146
  z: -0.1780717521905899
}
landmark {
  x: 0.13744059205055237
  y: 0.20520317554473877
  z: -0.20456469058990479
}
landmark {
  x: 0.3071948289871216
  y: 0.5886822938919067
  z: -0.0940912514925003
}
landmark {
  x: 0.3230797350406647

Handedness: [classification {
  index: 1
  score: 0.9943142533302307
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.6702255606651306
  y: 0.7315208911895752
  z: 0.0
}
landmark {
  x: 0.5816071033477783
  y: 0.6522352695465088
  z: -0.054792072623968124
}
landmark {
  x: 0.5592164993286133
  y: 0.5112395286560059
  z: -0.06933315098285675
}
landmark {
  x: 0.6405478715896606
  y: 0.4104682505130768
  z: -0.0831761360168457
}
landmark {
  x: 0.7216618061065674
  y: 0.35368242859840393
  z: -0.0928913950920105
}
landmark {
  x: 0.5939636826515198
  y: 0.40907034277915955
  z: 0.003322978038340807
}
landmark {
  x: 0.5594854950904846
  y: 0.27722567319869995
  z: -0.027579674497246742
}
landmark {
  x: 0.5500011444091797
  y: 0.18745501339435577
  z: -0.03993036597967148
}
landmark {
  x: 0.550413191318512
  y: 0.1096329391002655
  z: -0.05100061371922493
}
landmark {
  x: 0.67763352394104
  y: 0.42560482025146484
  z: -0.005993919912725687
}
landmark {
  x: 0.7252228260040283
  y

hand_landmarks: landmark {
  x: 0.35885146260261536
  y: 0.5649130940437317
  z: 0.0
}
landmark {
  x: 0.3036179840564728
  y: 0.49177706241607666
  z: -0.025115016847848892
}
landmark {
  x: 0.2889004051685333
  y: 0.39776983857154846
  z: -0.036211758852005005
}
landmark {
  x: 0.337550550699234
  y: 0.32993727922439575
  z: -0.050870005041360855
}
landmark {
  x: 0.3921578824520111
  y: 0.2918255925178528
  z: -0.061818212270736694
}
landmark {
  x: 0.31682994961738586
  y: 0.32846391201019287
  z: 0.008626232855021954
}
landmark {
  x: 0.30081906914711
  y: 0.2327229380607605
  z: -0.018399015069007874
}
landmark {
  x: 0.2948276698589325
  y: 0.17384392023086548
  z: -0.03050912916660309
}
landmark {
  x: 0.29529279470443726
  y: 0.12177559733390808
  z: -0.037998225539922714
}
landmark {
  x: 0.37184038758277893
  y: 0.3394136428833008
  z: -0.002657497301697731
}
landmark {
  x: 0.3978113532066345
  y: 0.2281228005886078
  z: -0.03107263147830963
}
landmark {
  x: 0.411185622215

Handedness: [classification {
  index: 1
  score: 0.9779601097106934
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.2541200816631317
  y: 0.6043922901153564
  z: 0.0
}
landmark {
  x: 0.18432873487472534
  y: 0.5024773478507996
  z: -0.033941514790058136
}
landmark {
  x: 0.17197385430335999
  y: 0.3777262270450592
  z: -0.04131587594747543
}
landmark {
  x: 0.2367057502269745
  y: 0.28655216097831726
  z: -0.05261819437146187
}
landmark {
  x: 0.3003116548061371
  y: 0.22962334752082825
  z: -0.05898192524909973
}
landmark {
  x: 0.20092442631721497
  y: 0.28530415892601013
  z: 0.030097099021077156
}
landmark {
  x: 0.17229215800762177
  y: 0.1713426411151886
  z: 0.0008584770257584751
}
landmark {
  x: 0.15812110900878906
  y: 0.1003323346376419
  z: -0.01222270168364048
}
landmark {
  x: 0.1523713320493698
  y: 0.035672515630722046
  z: -0.01980837807059288
}
landmark {
  x: 0.26915442943573
  y: 0.300615519285202
  z: 0.020215440541505814
}
landmark {
  x: 0.30621632933616

Handedness: [classification {
  index: 1
  score: 0.9833791255950928
  label: "Right"
}
]
hand_landmarks: landmark {
  x: 0.4380528926849365
  y: 0.6020825505256653
  z: 0.0
}
landmark {
  x: 0.3767881393432617
  y: 0.556755542755127
  z: -0.022764353081583977
}
landmark {
  x: 0.3507572412490845
  y: 0.47673535346984863
  z: -0.03353777900338173
}
landmark {
  x: 0.38084927201271057
  y: 0.41907504200935364
  z: -0.04738137125968933
}
landmark {
  x: 0.425017386674881
  y: 0.39756160974502563
  z: -0.05924762412905693
}
landmark {
  x: 0.3761800527572632
  y: 0.43136313557624817
  z: 0.0012524272315204144
}
landmark {
  x: 0.3503614664077759
  y: 0.36030304431915283
  z: -0.02308279648423195
}
landmark {
  x: 0.3410422205924988
  y: 0.31670188903808594
  z: -0.03781653195619583
}
landmark {
  x: 0.338604599237442
  y: 0.2777702212333679
  z: -0.04732145741581917
}
landmark {
  x: 0.42349714040756226
  y: 0.44117265939712524
  z: -0.005224929191172123
}
landmark {
  x: 0.42821377515792

In [9]:
print("Dataframe Contents ", dfObj, sep='\n')

Dataframe Contents 
     LetterLabel                                         Handedness  \
0              k  [classification {\n  index: 1\n  score: 0.9886...   
1              k  [classification {\n  index: 1\n  score: 0.9837...   
2              k  [classification {\n  index: 1\n  score: 0.9822...   
3              k  [classification {\n  index: 1\n  score: 0.9953...   
4              k  [classification {\n  index: 1\n  score: 0.9946...   
...          ...                                                ...   
2430           k  [classification {\n  index: 1\n  score: 0.9833...   
2431           k  [classification {\n  index: 1\n  score: 0.9833...   
2432           k  [classification {\n  index: 1\n  score: 0.9637...   
2433           k  [classification {\n  index: 1\n  score: 0.9784...   
2434           k  [classification {\n  index: 1\n  score: 0.9876...   

                                              Landmarks  
0     landmark {\n  x: 0.4801557660102844\n  y: 0.83...  
1     landm

In [ ]:
import numpy as np
from numpy import savetxt

In [ ]:
tmp = np.array(all_img_features,dtype = object)
savetxt('k.csv', tmp,fmt='%s')

In [ ]:
tmp[0]

# for multiple folders

In [ ]:
directory = '/Users/bridgetliu/project/mais2021/archive/asl_alphabet_train/asl_alphabet_train/'
count = 0 
names = []
folders = []
for root, subdirectories, files in os.walk(directory):
    for subdirectory in subdirectories:
        count +=1
        #print(os.path.join(root, subdirectory))
        # loop thru all the files in a folder 
        filenames = []
        directory = os.path.join(root, subdirectory)
        for filename in os.listdir(directory):
            if filename.endswith(".jpg") or filename.endswith(".png"):
                filenames.append(os.path.join(directory, filename))
            else:
                continue
        names.append(filenames)
        folders.append(subdirectory)

In [ ]:
len(names[0])

In [ ]:
count

In [ ]:
folder

In [ ]:
import cv2
import mediapipe as mp
mp_drawing = mp.solutions.drawing_utils
mp_drawing_styles = mp.solutions.drawing_styles
mp_hands = mp.solutions.hands

## nope this is taking too long 

for i in range(29):
    IMAGE_FILES = names[i]
    all_img_features = []
    with mp_hands.Hands(
        static_image_mode=True,
        max_num_hands=2,
        min_detection_confidence=0.5) as hands:
        for idx, file in enumerate(IMAGE_FILES):
            print("here")
            featurelist = []
            # Read an image, flip it around y-axis for correct handedness output
            image = cv2.flip(cv2.imread(file), 1)
            # Convert the BGR image to RGB before processing.
            results = hands.process(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
            #results = hands.process(image)
            #Print handedness and draw hand landmarks on the image.
            featurelist.append(folders[i])
            featurelist.append(results.multi_handedness)
            print('Handedness:', results.multi_handedness)
            if not results.multi_hand_landmarks:
                continue
        
            image_height, image_width, _ = image.shape
            annotated_image = image.copy()
        
            for hand_landmarks in results.multi_hand_landmarks:
                featurelist.append(hand_landmarks)
                print('hand_landmarks:', hand_landmarks)
                print(
                   f'Index finger tip coordinates: (',
                   f'{hand_landmarks.landmark[mp_hands.HandLandmark.INDEX_FINGER_TIP].x * image_width}, '
                   f'{hand_landmarks.landmark[mp_hands.HandLandmark.INDEX_FINGER_TIP].y * image_height})'
                )
            '''
            mp_drawing.draw_landmarks(
               annotated_image,
               hand_landmarks,
               mp_hands.HAND_CONNECTIONS,
               mp_drawing_styles.get_default_hand_landmarks_style(),
               mp_drawing_styles.get_default_hand_connections_style())
            '''
            #cv2.imwrite(
            #'/Users/bridgetliu/project/mais2021/tmp'+str(idx)+'.png', cv2.flip(annotated_image, 1))
            all_img_features.append(featurelist)


In [ ]:
tmp = np.array(all_img_features,dtype = object)
savetxt('features.csv', tmp,fmt='%s')